In [1]:
import pandas  as pd 
from itertools import product
from collections import defaultdict

Estado actual: 
* Pandas es muy lento para lo que quiero hacer
* Trabajo actual: separar los desempates en: Primero wins, despues rounds, despues mapas (probablemente no se implemente)
* Potenciales soluciones: Cambiar la manera de armar la tabla a Numpy (deberia ser lo mas rapido por mucho) Ventajas: velocidad y puedo evaluar por filas los resultados 

-------------------------------------------------------------------------

Arranco casi de 0, problemas con la unicacion de memoria de los objetos y se armo un re quilombo. 
Intento 2 diseño enfocado tabla final que tengo y estructurar desde ese punto hacia atras. 



In [2]:
#Esto es raro, siento que estoy dando vueltas en circulo con este diccionario creando los objetos y volviendo a usarlos 
#Lo termino usando con un zip, lo que puede ser peligroso con el orden y las keys
teamNameScores = {
                "name": ["Kru","Lev","100T","mibr","NRG","EG","FUR","LOUD", "2G","GAMERS2","C9","SEN"],
                "wins": [6,9,5,1,4,4,3,4,7,00,6,6],
                "loss":[4,1,5,9,6,6,7,6,3,00,4,4],
                "matchWins" : [15,19,12,3,10,10,8,11,15,00,13,13],
                "matchLoss" : [10,4,11,18,13,15,15,14,8,00,13,8],
                "roundWin":[287,296,255,168,238,241,195,249,249,00,270,249],
                "roundLoss":[247,204,232,257,237,281,270,275,214,00,276,214]
                
                  }

roundMatches = {
                "week11" : [["Kru","Lev"], ["100T","mibr"],["NRG","EG"], ["FUR","LOUD"],["2G","GAMERS2"],["C9","SEN"]],
                "week12" : [["Kru","100T"], ["Lev","mibr"],["NRG","FUR"], ["EG","LOUD"],["C9","GAMERS2"],["2G","SEN"]]
                }

In [3]:
teamNameScores = {
    "name": [
        "Kru",
        "Lev",
        "100T",
        "mibr",
        "NRG",
        "EG",
        "FUR",
        "LOUD",
        "2G",
        "GAMERS2",
        "C9",
        "SEN",
    ],
    "wins": [0, 0, 0, 0, 0, 0, 0, 0, 0, 00, 0, 0],
    "loss": [0, 0, 0, 0, 0, 0, 0, 0, 0, 00, 0, 0],
    "matchWins": [0, 0, 0,0, 0, 0,0, 0, 0, 0, 0, 0],
    "matchLoss": [0,0, 0, 0, 0, 0, 0, 0,0, 0, 0, 0],
    "roundWin": [0, 0, 0, 0, 0, 0, 0, 0, 0,0, 0, 0],
    "roundLoss": [0, 0, 0, 0, 0, 0, 0, 0, 0,0, 0, 0],
}

roundMatches = {
    "week11": [
        ["Kru", "Lev"],
        ["100T", "mibr"],
        ["NRG", "EG"],
        ["FUR", "LOUD"],
        ["2G", "GAMERS2"],
        ["C9", "SEN"],
    ],
    "week12": [
        ["Kru", "100T"],
        ["Lev", "mibr"],
        ["NRG", "FUR"],
        ["EG", "LOUD"],
        ["C9", "GAMERS2"],
        ["2G", "SEN"],
    ],
}

In [5]:
def run_round(matches, teams, previous_results=None):
    if previous_results is None: #Esto se queda por ser solo 1 UP 
        previous_results = []
        for i, team in enumerate(teams["name"]):
            temp_dict = {
                "UP": 1,
                "Team": team,
                "wins": teams["wins"][i],
                "matchWins": teams["matchWins"][i],
                "matchLoss": teams["matchLoss"][i],
            }
            previous_results.append(temp_dict)

    match_outcomes = list(product([0, 1, 2, 3], repeat=len(matches)))
    new_results = []

    result_mapping = {
        0: (0, 2),  # pierde 0-2
        1: (1, 2),  # pierde 1-2
        2: (2, 1),  # gana 2-1
        3: (2, 0),  # gana 2-0
    }

    test_group = defaultdict(list)
    for result in previous_results:
        test_group[result["UP"]].append(result)

    for up, group in test_group.items():
        simul_teams = {
            team_data["Team"]: {
                "wins": team_data["wins"],
                "matchWins": team_data["matchWins"],
                "matchLoss": team_data["matchLoss"],
            }
            for team_data in group}

        for combination_index, combination in enumerate(match_outcomes, start=1):

            temp_teams = {team: data.copy() for team, data in simul_teams.items()}

            for match_index, result in enumerate(combination):
                team1, team2 = matches[match_index]
                team1_score, team2_score = result_mapping[result]

                if result in [2, 3]:
                    temp_teams[team1]["wins"] += 1
                    temp_teams[team1]["matchWins"] += team1_score
                    temp_teams[team1]["matchLoss"] += team2_score
                    temp_teams[team2]["matchWins"] += team2_score
                    temp_teams[team2]["matchLoss"] += team1_score

                else:
                    temp_teams[team2]["wins"] += 1
                    temp_teams[team2]["matchWins"] += team2_score
                    temp_teams[team2]["matchLoss"] += team1_score
                    temp_teams[team1]["matchWins"] += team1_score
                    temp_teams[team1]["matchLoss"] += team2_score

            new_up = f"{up}-{combination_index}"

            for team, data in temp_teams.items():
                new_results.append(
                    {
                        "UP": new_up,
                        "Team": team,
                        "wins": data["wins"],
                        "matchWins": data["matchWins"],
                        "matchLoss": data["matchLoss"],
                    }
                )

    return new_results

In [6]:
teams = teamNameScores
matches = (("Kru","Lev"), ("100T","mibr"),("NRG","EG"), ("FUR","LOUD"),("2G","GAMERS2"),("C9","SEN"))
matches2 = [["Kru","100T"], ["Lev","mibr"],["NRG","FUR"], ["EG","LOUD"],["C9","GAMERS2"],["2G","SEN"]]


In [7]:
match1_results = run_round(matches, teams)

In [10]:
len(match1_results)/12

4096.0

In [81]:
match1_results

[{'UP': '1-1', 'Team': 'Kru', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'Lev', 'wins': 1, 'matchWins': 2, 'matchLoss': 0},
 {'UP': '1-1', 'Team': '100T', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'mibr', 'wins': 1, 'matchWins': 2, 'matchLoss': 0},
 {'UP': '1-1', 'Team': 'NRG', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'EG', 'wins': 1, 'matchWins': 2, 'matchLoss': 0},
 {'UP': '1-1', 'Team': 'FUR', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'LOUD', 'wins': 1, 'matchWins': 2, 'matchLoss': 0},
 {'UP': '1-1', 'Team': '2G', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'GAMERS2', 'wins': 1, 'matchWins': 2, 'matchLoss': 0},
 {'UP': '1-1', 'Team': 'C9', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'SEN', 'wins': 1, 'matchWins': 2, 'matchLoss': 0},
 {'UP': '1-2', 'Team': 'Kru', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-2', 'Team': 'Lev', 'win

In [83]:
def groupby_UP(matchresults):
    group_result = defaultdict(list)
    for result in matchresults:
        group_result[result["UP"]].append(result)
    return group_result

In [93]:
def heriarchy_dict_for_sort(groupby_up_dict):
    hierarchy_dict_to_return = {}
    for key in groupby_up_dict.keys():
        hierarchy_dict_to_append = {}
        for team in groupby_up_dict[key]:
            hierarchy_dict_to_append[team["Team"]] = {
                "wins": team["wins"],
                "matchWins": team["matchWins"],
                "matchLoss": team["matchLoss"],
            }
        hierarchy_dict_to_return[key] = hierarchy_dict_to_append
    return hierarchy_dict_to_return



In [85]:
groupby_up = groupby_UP(match1_results)


In [94]:
dict_ready_to_sort = heriarchy_dict_for_sort(groupby_up)

In [96]:
(dict_ready_to_sort)

{'1-1': {'Kru': {'wins': 0, 'matchWins': 0, 'matchLoss': 2},
  'Lev': {'wins': 1, 'matchWins': 2, 'matchLoss': 0},
  '100T': {'wins': 0, 'matchWins': 0, 'matchLoss': 2},
  'mibr': {'wins': 1, 'matchWins': 2, 'matchLoss': 0},
  'NRG': {'wins': 0, 'matchWins': 0, 'matchLoss': 2},
  'EG': {'wins': 1, 'matchWins': 2, 'matchLoss': 0},
  'FUR': {'wins': 0, 'matchWins': 0, 'matchLoss': 2},
  'LOUD': {'wins': 1, 'matchWins': 2, 'matchLoss': 0},
  '2G': {'wins': 0, 'matchWins': 0, 'matchLoss': 2},
  'GAMERS2': {'wins': 1, 'matchWins': 2, 'matchLoss': 0},
  'C9': {'wins': 0, 'matchWins': 0, 'matchLoss': 2},
  'SEN': {'wins': 1, 'matchWins': 2, 'matchLoss': 0}},
 '1-2': {'Kru': {'wins': 0, 'matchWins': 0, 'matchLoss': 2},
  'Lev': {'wins': 1, 'matchWins': 2, 'matchLoss': 0},
  '100T': {'wins': 0, 'matchWins': 0, 'matchLoss': 2},
  'mibr': {'wins': 1, 'matchWins': 2, 'matchLoss': 0},
  'NRG': {'wins': 0, 'matchWins': 0, 'matchLoss': 2},
  'EG': {'wins': 1, 'matchWins': 2, 'matchLoss': 0},
  'FUR':

In [107]:
from itertools import groupby

def group_table(teamDict):
    return  [
    list(group) for _, group in groupby(teamDict, key=lambda x: x[1]["wins"])
    ]  

In [108]:
def sort_dict_by_wins(single_up_round):
    sorted_table = sorted(single_up_round.items(), key =lambda x: (x[1]["wins"]), reverse=True)
    
    grouped_table = group_table(sorted_table)   
    return grouped_table

#Aca tengo que agregar el desempate y los resultados y no crear todo la lista larga 

In [151]:
def untie(up_dict_sorted, dict_head2head,dict_up_position):
    positon = 1
    #print(test_sort)
    for list_team in up_dict_sorted:
        if len(list_team) > 1:
            for team in list_team:
                 print(team, positon)
                 positon += 1
    
    return

In [152]:
untie(test_sort, test_sort,test_sort)

('Lev', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}) 1
('mibr', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}) 2
('EG', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}) 3
('LOUD', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}) 4
('GAMERS2', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}) 5
('C9', {'wins': 1, 'matchWins': 2, 'matchLoss': 1}) 6
('Kru', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}) 7
('100T', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}) 8
('NRG', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}) 9
('FUR', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}) 10
('2G', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}) 11
('SEN', {'wins': 0, 'matchWins': 1, 'matchLoss': 2}) 12


In [127]:
dict_up_position = {}
for team in teamNameScores["name"]:
        dict_up_position[team] = {
            "rank1": 0,
            "rank2": 0,
            "rank3": 0,
            "rank4": 0,
            "rank6": 0,
            "rank7": 0,
            "rank8": 0,
            "rank9": 0,
            "rank10": 0,
            "rank11": 0,
            "rank12": 0,            
            }


In [124]:
sorted_values = sorted_list_of_up_dict(dict_ready_to_sort)

In [130]:
test_sort = sort_dict_by_wins(dict_ready_to_sort["1-3"])

In [122]:
sorted_result = []

for key in dict_ready_to_sort.keys():
    single_up_sorted = sort_dict_by_wins(dict_ready_to_sort[key])
    sorted_result.append(single_up_sorted)
    

In [121]:
sorted_result

[[[('Lev', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('mibr', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('EG', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('LOUD', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('GAMERS2', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('SEN', {'wins': 1, 'matchWins': 2, 'matchLoss': 0})],
  [('Kru', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}),
   ('100T', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}),
   ('NRG', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}),
   ('FUR', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}),
   ('2G', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}),
   ('C9', {'wins': 0, 'matchWins': 0, 'matchLoss': 2})]],
 [[('Lev', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('mibr', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('EG', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('LOUD', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('GAMERS2', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('SEN', {'wins':

In [73]:
sorted_table =  sorted(test_hierarchy_dict.items(), key =lambda x: (x[1]["wins"]), reverse=True) 



In [80]:
for up in heriarchy_dict_multiple:
    print(sorted(test_hierarchy_dict.items(), key =lambda x: (x[1]["wins"]), reverse=True) )

[('Kru', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}), ('100T', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}), ('NRG', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}), ('FUR', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}), ('2G', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}), ('C9', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}), ('Lev', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}), ('mibr', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}), ('EG', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}), ('LOUD', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}), ('GAMERS2', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}), ('SEN', {'wins': 0, 'matchWins': 0, 'matchLoss': 2})]
[('Kru', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}), ('100T', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}), ('NRG', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}), ('FUR', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}), ('2G', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}), ('C9', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}), ('Lev', {'wins': 0, 'ma

In [74]:
sorted_table

[('Lev', {'wins': 1, 'matchWins': 2, 'matchLoss': 0, 'deltaMatch': 2}),
 ('mibr', {'wins': 1, 'matchWins': 2, 'matchLoss': 0, 'deltaMatch': 2}),
 ('EG', {'wins': 1, 'matchWins': 2, 'matchLoss': 0, 'deltaMatch': 2}),
 ('LOUD', {'wins': 1, 'matchWins': 2, 'matchLoss': 0, 'deltaMatch': 2}),
 ('GAMERS2', {'wins': 1, 'matchWins': 2, 'matchLoss': 0, 'deltaMatch': 2}),
 ('SEN', {'wins': 1, 'matchWins': 2, 'matchLoss': 0, 'deltaMatch': 2}),
 ('Kru', {'wins': 0, 'matchWins': 0, 'matchLoss': 2, 'deltaMatch': -2}),
 ('100T', {'wins': 0, 'matchWins': 0, 'matchLoss': 2, 'deltaMatch': -2}),
 ('NRG', {'wins': 0, 'matchWins': 0, 'matchLoss': 2, 'deltaMatch': -2}),
 ('FUR', {'wins': 0, 'matchWins': 0, 'matchLoss': 2, 'deltaMatch': -2}),
 ('2G', {'wins': 0, 'matchWins': 0, 'matchLoss': 2, 'deltaMatch': -2}),
 ('C9', {'wins': 0, 'matchWins': 0, 'matchLoss': 2, 'deltaMatch': -2})]

In [66]:
for i in (test_group["1-1"]):
    print(i["UP"])
    

1-1
1-1
1-1
1-1
1-1
1-1
1-1
1-1
1-1
1-1
1-1
1-1


In [44]:
from itertools import groupby
for elements in test_group["1-1"]:
    for key, group in groupby(elements, lambda x: x):
        for min in group:
            print(min)

UP
Team
wins
matchWins
matchLoss
UP
Team
wins
matchWins
matchLoss
UP
Team
wins
matchWins
matchLoss
UP
Team
wins
matchWins
matchLoss
UP
Team
wins
matchWins
matchLoss
UP
Team
wins
matchWins
matchLoss
UP
Team
wins
matchWins
matchLoss
UP
Team
wins
matchWins
matchLoss
UP
Team
wins
matchWins
matchLoss
UP
Team
wins
matchWins
matchLoss
UP
Team
wins
matchWins
matchLoss
UP
Team
wins
matchWins
matchLoss


In [36]:
from itertools import groupby
for equipo in test_group["1-1"]:
   test_groupby =  [list(group) for _, group in groupby(test_group, key=lambda x: x[1]["wins"])
    ]
    


TypeError: string indices must be integers, not 'str'

In [34]:
test_groupby

[{'UP': '1-1', 'Team': 'Kru', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'Lev', 'wins': 1, 'matchWins': 2, 'matchLoss': 0},
 {'UP': '1-1', 'Team': '100T', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'mibr', 'wins': 1, 'matchWins': 2, 'matchLoss': 0},
 {'UP': '1-1', 'Team': 'NRG', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'EG', 'wins': 1, 'matchWins': 2, 'matchLoss': 0},
 {'UP': '1-1', 'Team': 'FUR', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'LOUD', 'wins': 1, 'matchWins': 2, 'matchLoss': 0},
 {'UP': '1-1', 'Team': '2G', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'GAMERS2', 'wins': 1, 'matchWins': 2, 'matchLoss': 0},
 {'UP': '1-1', 'Team': 'C9', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'SEN', 'wins': 1, 'matchWins': 2, 'matchLoss': 0}]

In [98]:
round1_df = pd.DataFrame(match1_results)

In [101]:
test_woking = round1_df

In [99]:
round1_df[round1_df["Team"] == "Lev"]

UP Team  wins  matchWins  matchLoss
1         1-1  Lev     1          2          0
13        1-2  Lev     1          2          0
25        1-3  Lev     1          2          0
37        1-4  Lev     1          2          0
49        1-5  Lev     1          2          0
...       ...  ...   ...        ...        ...
49093  1-4092  Lev     0          0          2
49105  1-4093  Lev     0          0          2
49117  1-4094  Lev     0          0          2
49129  1-4095  Lev     0          0          2
49141  1-4096  Lev     0          0          2

[4096 rows x 5 columns]

In [115]:
round1_df.wins.value_counts()

0    24576
1    24576
Name: wins, dtype: int64

In [11]:
match2_results = run_round(matches, teams, match1_results)

In [117]:
round2_df = pd.DataFrame(match2_results)

In [124]:
round2_df[500000:600000].head()

UP     Team  wins  matchWins  matchLoss
500000  1-1007-707       2G     1          2          2
500001  1-1007-707  GAMERS2     1          2          2
500002  1-1007-707       C9     2          4          2
500003  1-1007-707      SEN     0          2          4
500004  1-1007-708      Kru     0          0          4

In [128]:
matches = (("Kru","Lev"), ("100T","mibr"),("NRG","EG"), ("FUR","LOUD"),("2G","GAMERS2"),("C9","SEN"))

In [31]:
test_group["1-1"]

[{'UP': '1-1', 'Team': 'Kru', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'Lev', 'wins': 1, 'matchWins': 2, 'matchLoss': 0},
 {'UP': '1-1', 'Team': '100T', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'mibr', 'wins': 1, 'matchWins': 2, 'matchLoss': 0},
 {'UP': '1-1', 'Team': 'NRG', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'EG', 'wins': 1, 'matchWins': 2, 'matchLoss': 0},
 {'UP': '1-1', 'Team': 'FUR', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'LOUD', 'wins': 1, 'matchWins': 2, 'matchLoss': 0},
 {'UP': '1-1', 'Team': '2G', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'GAMERS2', 'wins': 1, 'matchWins': 2, 'matchLoss': 0},
 {'UP': '1-1', 'Team': 'C9', 'wins': 0, 'matchWins': 0, 'matchLoss': 2},
 {'UP': '1-1', 'Team': 'SEN', 'wins': 1, 'matchWins': 2, 'matchLoss': 0}]

In [30]:
from itertools import groupby

sorted_table = sorted(test_group["1-1"].items(), 
                              key = lambda x: (x[1]["wins"],x[1]["loss"],
                                               x[1]["matchWins"],x[1]["matchLoss"],
                                               x[1]["matchRanking"],
                                               x[1]["rivals"]),        
        reverse=True)

TypeError: string indices must be integers, not 'str'

In [ ]:
match2_results = run_round2(matches, teams,match1_results)

{'Kru': {'wins': 1, 'matchWins': 2, 'matchLoss': 0}, 'Lev': {'wins': 0, 'matchWins': 0, 'matchLoss': 2}, '100T': {'wins': 1, 'matchWins': 2, 'matchLoss': 0}, 'mibr': {'wins': 0, 'matchWins': 0, 'matchLoss': 2}, 'NRG': {'wins': 1, 'matchWins': 2, 'matchLoss': 0}, 'EG': {'wins': 0, 'matchWins': 0, 'matchLoss': 2}, 'FUR': {'wins': 1, 'matchWins': 2, 'matchLoss': 0}, 'LOUD': {'wins': 0, 'matchWins': 0, 'matchLoss': 2}, '2G': {'wins': 1, 'matchWins': 2, 'matchLoss': 0}, 'GAMERS2': {'wins': 0, 'matchWins': 0, 'matchLoss': 2}, 'C9': {'wins': 1, 'matchWins': 2, 'matchLoss': 0}, 'SEN': {'wins': 0, 'matchWins': 0, 'matchLoss': 2}}


In [24]:
len(match2_results)

201326592

In [135]:
def run_round2(matches, teams, previous_results=None):
    if previous_results is None:
        previous_results = [
            {
                "UP": 1,
                "Team": team,
                "wins": data["wins"],
                "matchWins": data["matchWins"],
                "matchLoss": data["matchLoss"],
            }
            for team, data in teams.items()
        ]

    match_outcomes = list(product([0, 1, 2, 3], repeat=len(matches)))
    new_results = []

    result_mapping = {
        0: (0, 2),  # pierde 0-2
        1: (1, 2),  # pierde 1-2
        2: (2, 1),  # gana 2-1
        3: (2, 0),  # gana 2-0
    }
    setUP = set()
    for result in previous_results:
        setUP.add(result["UP"])
    #print(setUP)
    
   
    
    for up in setUP:        
        simul_teams = {}
        for result in previous_results:
   
            simul_teams[result["Team"]] = {
                "wins": result["wins"],
                "matchWins": result["matchWins"],
                "matchLoss": result["matchLoss"],
            }
            
        for combination_index, combination in enumerate(match_outcomes, start=1):
            temp_teams = {team: data.copy() for team, data in simul_teams.items()}

            for match_index, result in enumerate(combination):
                team1, team2 = matches[match_index]
                team1_score, team2_score = result_mapping[result]

                #print(result)
                if result in [2, 3]:
                    temp_teams[team1]["wins"] += 1
                    temp_teams[team1]["matchWins"] += team1_score
                    temp_teams[team1]["matchLoss"] += team2_score
                    temp_teams[team2]["matchWins"] += team2_score
                    temp_teams[team2]["matchLoss"] += team1_score
                    # print(team1, team2, match_wins, match_loss)

                else:
                    temp_teams[team2]["wins"] += 1
                    temp_teams[team2]["matchWins"] += team2_score
                    temp_teams[team2]["matchLoss"] += team1_score
                    temp_teams[team1]["matchWins"] += team1_score
                    temp_teams[team1]["matchLoss"] += team2_score

            new_up = f"{up}-{combination_index}"

            for team, data in temp_teams.items():
                new_results.append(
                    {
                        "UP": new_up,
                        "Team": team,
                        "wins": data["wins"],
                        "matchWins": data["matchWins"],
                        "matchLoss": data["matchLoss"],
                    }
                )            
    return new_results